In [1]:
import sys
sys.path.append('../')

from config import sentence_fname, zcorpus_fname, feature_manager_fname
from config import word2vec_model_fname
from simple_ner import Sentences
from simple_ner import FeatureCountingNER, FeatureManager, ZCorpus

## Training Word2Vec

In [2]:
# from gensim.models import Word2Vec
# sentences = Sentences(sentence_fname)
# word2vec = Word2Vec(sentences, min_count=20, window=3)

import pickle
# with open(word2vec_model_fname, 'wb') as f:
#     pickle.dump(word2vec, f)
with open(word2vec_model_fname, 'rb') as f:
    word2vec = pickle.load(f)
    
print('Word2Vec training was done')

Word2Vec training was done


### Select seed words

In [3]:
# print(word2vec.most_similar('비빔면', topn=50))
# print(word2vec.most_similar('양꼬치', topn=50))

snacks = {snack for snack, sim in word2vec.most_similar('비빔면', topn=50)}
snacks.update({snack for snack, sim in word2vec.most_similar('컵라면', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('치킨', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('야식', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('안주', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('소고기', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('바나나우유', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('양꼬치', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('곱창', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('스시', topn=50)})
snacks.update({snack for snack, sim in word2vec.most_similar('조개', topn=50)})
len(snacks)

253

In [4]:
'  '.join(snacks)

'햄벅  빈대떡  팥죽  채소  인스턴트  고로케  홍어  크레페  치폴레  수제비  떡튀순  문어  콜라  삼김  짜왕  꽃게  복숭아  요구르트  쌈도  야식  한우  칼국수  해물찜  쌀밥  육개장  골뱅이  후식  아구찜  컵밥  음료수  고기  낙지  유자차  조개구이  비비큐  꼬치  케익  꼬기  청국장  갈비탕  닭발  피자  킹크랩  견과류  에스프레소  훠궈  샤브  엽떡  쫄면  아점  상추  소스  가래떡  석식  쿨피스  삼치  프링글스  카레  식혜  키위  맥주  석류  짜파게티  순대국  씨리얼  컵라면  초밥  껍데기  와플  비빔밥  치킨  음료  헛개수  뼈해장국  등갈비  갈비  두부  핫도그  라멘  잡채밥  파닭  순대  밀크티  호떡  치맥  미숫가루  떡볶이  소고기  햄버거  갈비찜  닭도  포카리  불고기  딤섬  타코야끼  김밥  탕수육  미역국  먹이  장어  갈매기살  청심환  삼겹살  광어  삼겹  수박  곱창  핫식스  풀떼기  팥빙수  마늘  쌈은  간식  주먹밥  김치찌개  닭강정  식초  월남쌈  국밥  브런치  블루베리  양꼬치  감자  홈런볼  호박죽  우유  쟁반짜장  스무디  빙수  쌈이랑  맥모닝  쌀국수  소주  과일  싸이버거  고등어  감튀  밀가루  소맥  컵누들  햇반  분식  닭갈비  떡갈비  족발  쉐이크  닭도리탕  반마리  바나나  보드카  고구마  분유  환타  쥐포  참외  뻥튀기  홍시  해장국  감자탕  살안찌  육포  소세지  양파  버블티  송편  깐풍기  파전  순두부  브리또  옥수수  츄러스  쥬스  치즈  짜장면  소금구이  쌈이  찜닭  백숙  곰국  콩국수  스시  라묜  팝콘  닭백숙  돈까스  야채  오징어  참치  연어  커리  빅맥  새우  삼계탕  토마토  닭꼬치  닭가슴살  간장게장  칙힌  갈치  물회  냉면  꼼장어  오뎅탕  돈부리  생선구이  티라미수  파스타  청하  타코  군만두  떡국  베지밀  설렁탕  아이스크림  북어국  라볶이

In [5]:
zcorpus = ZCorpus(zcorpus_fname)
for num_z, zi in enumerate(zcorpus):
    if num_z > 10: break
    print(zi)

('아뇨', ['4428'])
('내꺼', ['1666', '1637', '30215'])
('아닌데', ['1798', '2783', '185588', '1'])
('요', ['4007', '2202'])
('네', ['8514'])
('은이', ['75', '360453'])
('씨꺼', ['95', '8889', '754', '176323'])
('인가', ['10734', '325394', '15027'])
('보네요', ['404447', '1152'])
('저녁', ['1511'])
('약속', ['186', '10854', '10853'])


In [12]:
feature_manager = FeatureManager()
feature_manager.load(feature_manager_fname)
ner_extractor = FeatureCountingNER(feature_manager)

positive_features = ner_extractor.find_positive_features(zcorpus,
                                                         snacks,
                                                         min_count_positive_features=10)

scanning positive features was done


In [13]:
wordset = set(word2vec.wv.vocab.keys())
ner_extractor.compute_score_of_features(zcorpus,
                                        snacks,
                                        wordset)

scanning usage of positive features was done
computing score of features was done


In [15]:
ners = ner_extractor.extract_named_entities_from_zcorpus(zcorpus)
ners = [(w,max(1, ners[0][1])) for w in snacks] + ners

(138154000 in 146711922) 94.167 %

## 한방에

In [ ]:
ners = fit_and_extract_ner(zcorpus,
                           ner_seed,
                           wordset,
                           min_count_positive_features=10)
ners = [(w,max(1, ners[0][1])) for w in snacks] + ners